In [1]:
from all_imports import *

import _modules


 ### test init### 


In [2]:
# <--- Loading stored Cozie data from Main.py --->
%store -r participant_data_local

#stat_participants_data
# Settings
column_lst_items = ['q_general_location_area', 'ws_heart_rate', 'ws_latitude', 'ts_latitude', 'location_change', 'ws_walking_distance', 'ws_survey_count']
#Add another list that defines if it should sum or count? Useful?


#Function
result_dfs = []
for participant_id, df in participant_data_local.items(): #participant_data
    # Create a dictionary to store the information for the current participant
    participant_info = {'participant_id': participant_id, 'rows': df.shape[0], 'columns': df.shape[1]}

    # Count non-null values for each specified column
    for column_item in column_lst_items:
        column_name = column_item
        if column_item in df.columns:
            data_count = df[column_item].count()
            participant_info[column_name] = data_count
        else:
            participant_info[column_name] = 'n/a'

    # Convert the participant_info dictionary to a DataFrame
    result_df_participant = pd.DataFrame([participant_info])
    # Append the result DataFrame for the current participant to the list
    result_dfs.append(result_df_participant)

# Concatenate all DataFrames in the list along the rows
result_df = pd.concat(result_dfs, ignore_index=True)

experiment_stat_df = result_df
# Print the result DataFrame
display(experiment_stat_df)



participant_id   rows  columns  q_general_location_area  ws_heart_rate  \
0         esse00  16782      152                      221           5645   
1         esse02  42724      185                      119          11737   
2         esse07  18749      139                      100           5121   
3         esse08  40607      187                      136          17144   
4         esse09  15047      136                      104           8756   
5         esse10  41821      145                      106          12611   
6         esse11  35614      193                      100          10281   
7         esse13  59509      139                      146          24289   
8         esse14  27477      175                      102          11049   

   ws_latitude  ts_latitude  location_change  ws_walking_distance  \
0          221          273              273                 1997   
1          119         2459             2459                 3784   
2          100          460              460                 2662   
3          136          291              291                16712   
4          104           11               11                 3934   
5          106         1635             1635                 8283   
6          100         1637             1637                 4510   
7          146          885              885                13868   
8          102          281              281                 5884   

   ws_survey_count  
0              221  
1              119  
2              100  
3              136  
4              104  
5              106  
6              100  
7              146  
8              102

In [3]:
display(participant_data_local)

{'esse14':                              index_time id_participant  \
 0      2024-02-21 15:43:42.575000+08:00         esse14   
 1      2024-02-21 15:44:18.818000+08:00         esse14   
 2      2024-02-21 15:46:38.202000+08:00         esse14   
 3      2024-02-21 15:46:39.202000+08:00         esse14   
 4             2024-02-21 15:50:00+08:00         esse14   
 ...                                 ...            ...   
 27472         2024-03-27 21:50:00+08:00         esse14   
 27473  2024-03-27 21:53:39.607000+08:00         esse14   
 27474  2024-03-27 21:54:53.150000+08:00         esse14   
 27475  2024-03-27 21:59:12.525000+08:00         esse14   
 27476  2024-03-27 22:00:38.049000+08:00         esse14   
 
                                id_onesignal  \
 0      7c180ea0-068d-46e1-8a2b-bd0937e7f6c9   
 1      7c180ea0-068d-46e1-8a2b-bd0937e7f6c9   
 2      7c180ea0-068d-46e1-8a2b-bd0937e7f6c9   
 3      7c180ea0-068d-46e1-8a2b-bd0937e7f6c9   
 4      7c180ea0-068d-46e1-8a2b-bd0937e7

In [3]:
# <--- Plotly Graphs --->
#Settings:
start_date          = '2024-02-20'
end_date            = '2024-03-29'

# Plot
#_modules.Plot_heatmap_participant_data(participant_data_local, start_date, end_date, column='ws_heart_rate', operation='count')
#_modules.Plot_heatmap_participant_data(participant_data_local, start_date, end_date, column='ws_survey_count', operation='count')

# <--- Heatmaps --->
_modules.Plot_plotly_heatmap_participant_data(participant_data_local, start_date, end_date, column='q_general_location_area', operation='count')
_modules.Plot_plotly_heatmap_participant_data(participant_data_local, start_date, end_date, column='ws_heart_rate', operation='count')

# <--- Survey Responses --->
_modules.Plot_linechart_participant_data(participant_data_local, start_date, end_date, data='ws_survey_count')
_modules.Plot_linechart_participant_data(participant_data_local, start_date, end_date, data='ws_heart_rate', operation='count') #make this to a boxplot


In [5]:
# <--- Data Flagging --->

#All columns will combined in one flag column at the end, flag are defined by the aformentioned identifiers

### Settings:
threshold_speed      = 100           #movespeed based on distance between points in meters per minute
threshold_steps      = 35            #amount of steps taking between surveys from healthkit
threshold_distance   = 25            #distance between points based on direct pathway using haversine
threshold_time_ws    = 6             #min time needed between watch surveys in minutes
threshold_time_data  = 9             #max time to check if data was retreived before the ws in minutes

%store -r directory_data_processed_path
print(directory_data_processed_path)
%store -r identifier
print(identifier)

#ToDO RunNumbers adjustment

# Load the shapefile for the study region
study_region_shapefile = "C:/Users/gottk/OneDrive/GITHUB/calma-esse-heat-stress-internal/Esse/data/study_region"
study_region = gpd.read_file(study_region_shapefile)


# Assuming participant_data_local is a dictionary where keys are participant IDs and values are DataFrames
for participant_id, df in participant_data_local.items():
    df['timestamp_lambda'] = pd.to_datetime(df['timestamp_lambda'])
    df['c_difference_time_ws'] = pd.NaT  # Initialize new column with NaT (Not a Time) values
    df['c_distance_ws'] = np.nan  # Initialize new column for distance calculation
    df['c_ws_step_count'] = np.nan  # Initialize new column for maximum step count
    df['c_movespeed'] = np.nan  # Initialize new column for move speed
    df['flag_speed_threshold'] = np.nan  # Initialize flag column for speed threshold
    df['flag_steps_threshold'] = np.nan  # Initialize flag column for steps threshold
    df['flag_distance_threshold'] = np.nan  # Initialize flag column for distance threshold
    df['flag_time_threshold'] = np.nan  # Initialize flag column for time threshold
    df['flag_data_retrieved'] = np.nan  # Initialize flag column for data retrieval
    df['in_study_region'] = np.nan
    df['participant_id'] = participant_id  # Set the participant id column

    previous_timestamp_ws = None  # Initialize previous timestamp variable
    previous_lat, previous_lon = None, None  # Initialize previous latitude and longitude variables
    max_step_count = 0  # Initialize variable to store maximum step count
    current_day = None  # Initialize variable to store current day

    for index, row in df.iterrows():
        if pd.isna(row['ws_latitude']) or pd.isna(row['ws_longitude']):
            df.at[index, 'in_study_region'] = np.nan
        else:
            point = gpd.points_from_xy([row['ws_longitude']], [row['ws_latitude']])
            if study_region.contains(point[0]).any():
                df.at[index, 'in_study_region'] = np.nan
            else:
                df.at[index, 'in_study_region'] = 'NotRegion'

        
        # Update maximum step count
        max_step_count = max(max_step_count, row['ws_step_count'])

        # Check if timestamp_lambda has changed to a new day
        if previous_timestamp_ws is not None:
            if row['timestamp_lambda'].day != current_day:
                # Reset max_step_count to zero for a new day
                max_step_count = 0
                current_day = row['timestamp_lambda'].day

        if not pd.isnull(row['ws_survey_count']):  # Check if 'ws_survey_count' is not empty
            if previous_timestamp_ws is not None:
                # If it is not the first entry, calculate the time difference and store it in 'c_difference_time_ws'
                time_diff = row['timestamp_lambda'] - previous_timestamp_ws
                if time_diff.days < 0:
                    # Handle the case where time difference is negative due to day change
                    time_diff += pd.Timedelta(days=1)
                df.at[index, 'c_difference_time_ws'] = time_diff

                # Calculate distance using haversine_vector
                current_lat, current_lon = row['ws_latitude'], row['ws_longitude']
                if previous_lat is not None and previous_lon is not None:
                    distance = haversine_vector((previous_lat, previous_lon), (current_lat, current_lon), Unit.METERS)
                    distance = np.round(distance)  # Round distance to the nearest integer
                    df.at[index, 'c_distance_ws'] = distance
                else:
                    distance = 0

                # Calculate move speed
                if time_diff.total_seconds() > 0:
                    move_speed = distance / (time_diff.total_seconds() / 60)
                    move_speed_rounded = np.round(move_speed, 2)  # Round move speed to 2 decimal places
                    df.at[index, 'c_movespeed'] = move_speed_rounded
                else:
                    df.at[index, 'c_movespeed'] = np.nan

                # Flag for speed threshold
                if move_speed > threshold_speed:
                    df.at[index, 'flag_speed_threshold'] = 'Movespeed'
                else:
                    df.at[index, 'flag_speed_threshold'] = np.nan

                # Flag for steps threshold
                if max_step_count > threshold_steps:
                    df.at[index, 'flag_steps_threshold'] = 'StepCount'
                else:
                    df.at[index, 'flag_steps_threshold'] = np.nan

                # Flag for distance threshold
                if distance > threshold_distance:
                    df.at[index, 'flag_distance_threshold'] = np.nan
                else:
                    df.at[index, 'flag_distance_threshold'] = 'Distance'

                # Flag for time threshold
                if time_diff.total_seconds() / 3600 > threshold_time_ws:
                    df.at[index, 'flag_time_threshold'] = 'TimeDifference'
                else:
                    df.at[index, 'flag_time_threshold'] = np.nan

                # Update previous latitude and longitude for next iteration
                previous_lat, previous_lon = current_lat, current_lon

                # Check if 'q_general_location_envi' is either 'Indoor' or 'Other'
                if row['q_general_location_envi'] in ['Indoor', 'Other']:
                    df.at[index, 'flag_q_general_location_envi'] = 'Environment'
                else:
                    df.at[index, 'flag_q_general_location_envi'] = np.nan  # Set flag to NaN if condition not met

            # Check if data was retrieved within the threshold time for any specified column
            data_retrieved = False
            for col in ['ws_heart_rate', 'ws_step_count', 'ws_survey_count']:
                if not pd.isnull(row[col]):
                    time_diff_data = row['timestamp_lambda'] - pd.to_datetime(row[col])
                    if time_diff_data.total_seconds() / 60 <= threshold_time_data:
                        data_retrieved = True
                        break  # Exit the loop once data is found within the threshold time

            if data_retrieved:
                df.at[index, 'flag_data_retrieved'] = 'DataRetrieved'
            else:
                df.at[index, 'flag_data_retrieved'] = np.nan

            # Update previous timestamp only when 'ws_survey_count' is not empty for the current row
            previous_timestamp_ws = row['timestamp_lambda']

#debugging
    # Save CSV for participant IDs 'esse03' or 'esse08'
    #if participant_id in ['esse00', 'esse02']:
    #    df[['timestamp_lambda','ws_longitude', 'ws_latitude', 'ws_survey_count', 'ws_step_count', 'q_general_location_envi', 'c_difference_time_ws', 'c_distance_ws', 'c_ws_step_count', 'flag_q_general_location_envi']].to_csv(f"C:/Users/gottk/OneDrive/GITHUB/calma-esse-heat-stress-internal/Esse/data/debugging/{participant_id}_data.csv", index=False)

    # Print the updated DataFrame for other participant IDs
    print(f"Participant ID: {participant_id}")
    # Just to check, drop the NaN columns of time
    df = df.dropna(subset=['q_general_location_envi'])
    display(df[['participant_id', 'timestamp_lambda','ws_longitude', 'ws_latitude', 'ws_survey_count', 'q_general_location_envi', 'c_difference_time_ws', 'c_distance_ws', 'c_ws_step_count','c_movespeed', 'flag_q_general_location_envi', 'flag_speed_threshold', 'flag_steps_threshold', 'flag_distance_threshold', 'flag_time_threshold', 'flag_data_retrieved', 'in_study_region']])
    print("\n")


# Combine all the DataFrames into one DataFrame
combined_df = pd.concat(list(participant_data_local.values()), ignore_index=True)

# Define the file name
file_name = f"{identifier}_Cozie_processed.csv"

# Concatenate the directory path and file name
file_path = os.path.join(directory_data_processed_path, file_name)

# Save the combined DataFrame to a CSV file
combined_df.to_csv(file_path, index=False)

print(f"Combined DataFrame saved to: {file_path}")


                
### reload the data from processed and compare it to a previous save and combine them:
    






c:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed
2024-03-30_1216


C:\Users\gottk\AppData\Local\Temp\ipykernel_19092\3721689978.py:72: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0 days 00:35:39.981525' has dtype incompatible with datetime64[ns], please explicitly cast to a compatible dtype first.

C:\Users\gottk\AppData\Local\Temp\ipykernel_19092\3721689978.py:107: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'Distance' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.

C:\Users\gottk\AppData\Local\Temp\ipykernel_19092\3721689978.py:120: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'Environment' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.

C:\Users\gottk\AppData\Local\Temp\ipykernel_19092\3721689978.py:111: FutureWarning:

Setting an item of incompati

Participant ID: esse14


C:\Users\gottk\AppData\Local\Temp\ipykernel_19092\3721689978.py:99: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value 'StepCount' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.



participant_id           timestamp_lambda  ws_longitude  ws_latitude  \
1             esse14 2024-02-21 07:44:21.821735    103.770868     1.297063   
35            esse14 2024-02-21 08:20:01.803260    103.770898     1.297111   
106           esse14 2024-02-21 10:07:49.690064    103.773017     1.296261   
155           esse14 2024-02-21 11:36:34.914702    103.773156     1.296066   
673           esse14 2024-02-21 12:12:22.284011    103.782134     1.296333   
...              ...                        ...           ...          ...   
27461         esse14 2024-03-27 13:26:47.099781    103.772036     1.298477   
27464         esse14 2024-03-27 13:27:14.082602    103.772073     1.298474   
27468         esse14 2024-03-27 13:37:15.283003    103.772036     1.298489   
27473         esse14 2024-03-27 14:00:14.439842    103.771983     1.298510   
27476         esse14 2024-03-27 14:00:39.034556    103.772030     1.298481   

       ws_survey_count q_general_location_envi    c_difference_time_ws  \
1                  0.0                  Indoor                     NaT   
35                 1.0            Semi-Outdoor  0 days 00:35:39.981525   
106                2.0                  Indoor  0 days 01:47:47.886804   
155                3.0            Semi-Outdoor  0 days 01:28:45.224638   
673                4.0                 Outdoor  0 days 00:35:47.369309   
...                ...                     ...                     ...   
27461             97.0            Semi-Outdoor  0 days 01:46:11.302469   
27464             98.0            Semi-Outdoor  0 days 00:00:26.982821   
27468             99.0            Semi-Outdoor  0 days 00:10:01.200401   
27473            100.0            Semi-Outdoor  0 days 00:22:59.156839   
27476            101.0            Semi-Outdoor  0 days 00:00:24.594714   

       c_distance_ws  c_ws_step_count  c_movespeed  \
1                NaN              NaN          NaN   
35               NaN              NaN         0.00   
106            254.0              NaN         2.36   
155             27.0              NaN         0.30   
673            999.0              NaN        27.91   
...              ...              ...          ...   
27461          119.0              NaN         1.12   
27464            4.0              NaN         8.89   
27468            4.0              NaN         0.40   
27473            6.0              NaN         0.26   
27476            6.0              NaN        14.64   

      flag_q_general_location_envi flag_speed_threshold flag_steps_threshold  \
1                              NaN                  NaN                  NaN   
35                             NaN                  NaN                  NaN   
106                    Environment                  NaN                  NaN   
155                            NaN                  NaN                  NaN   
673                            NaN                  NaN                  NaN   
...                            ...                  ...                  ...   
27461                          NaN                  NaN            StepCount   
27464                          NaN                  NaN            StepCount   
27468                          NaN                  NaN            StepCount   
27473                          NaN                  NaN            StepCount   
27476                          NaN                  NaN            StepCount   

      flag_distance_threshold flag_time_threshold  flag_data_retrieved  \
1                         NaN                 NaN                  NaN   
35                   Distance                 NaN                  NaN   
106                       NaN                 NaN                  NaN   
155                       NaN                 NaN                  NaN   
673                       NaN                 NaN                  NaN   
...                       ...                 ...                  ...   
27461                     NaN                 NaN   



Combined DataFrame saved to: c:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed\2024-03-30_1216_Cozie_processed.csv


In [8]:
#COMAPRE FILES
#Now load a previous file and compare the two, take the data from the previous one prefereably on difference:
# Step 1: List all CSV files in the directory

%store -r directory_data_processed_path
print(directory_data_processed_path)
%store -r identifier
print(identifier)

columns_to_check = ['participant_id', 'timestamp_lambda','ws_longitude', 'ws_latitude', 'ws_survey_count', 'q_general_location_envi', 'c_difference_time_ws', 'c_distance_ws', 'c_ws_step_count','c_movespeed', 'flag_q_general_location_envi', 'flag_speed_threshold', 'flag_steps_threshold', 'flag_distance_threshold', 'flag_time_threshold', 'flag_data_retrieved']  # Update with actual column names

# List all CSV files in the directory
csv_files = [f for f in os.listdir(directory_data_processed_path) if f.endswith('.csv')]

# Sort the files by name (time)
csv_files.sort(reverse=True)

# Read the two newest CSV files into DataFrames
if len(csv_files) >= 2:
    newest_file = os.path.join(directory_data_processed_path, csv_files[0])
    second_newest_file = os.path.join(directory_data_processed_path, csv_files[1])
    print(newest_file)
    print(second_newest_file)

    newest_df = pd.read_csv(newest_file)
    second_newest_df = pd.read_csv(second_newest_file)

newest_df = r'C:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed\2024-03-30_1216_Cozie_processed - Copy.csv'
second_newest_df = r'C:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed\2024-03-30_1216_Cozie_processed.csv' 

# Function to compare rows and select rows from old_df if there's a difference
def select_rows(row):
    second_row = second_newest_df.iloc[row.name]  # Get corresponding row from the second DataFrame
    differences = any(row[col] != second_row[col] for col in columns_to_check)  # Check differences in specified columns
    if differences:
        return second_row  # Return row from second_newest_df if there's a difference
    else:
        return row  # Return row from newest_df if there's no difference

# Apply the function row-wise to the newest DataFrame
#new_df_rows = newest_df.apply(select_rows, axis=1)

# Create a new DataFrame with rows from new_df_rows
#new_df = pd.DataFrame(new_df_rows, columns=newest_df.columns)

new_df = pd.read_csv(newest_df)

display(new_df[['participant_id', 'timestamp_lambda','ws_longitude', 'ws_latitude', 'ws_survey_count', 'q_general_location_envi', 'c_difference_time_ws', 'c_distance_ws', 'c_ws_step_count','c_movespeed', 'flag_q_general_location_envi', 'flag_speed_threshold', 'flag_steps_threshold', 'flag_distance_threshold', 'flag_time_threshold', 'flag_data_retrieved', 'in_study_region']])


c:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed
2024-04-02_1102
c:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed\2024-04-02_1102_Cozie_main_df.csv
c:\Users\gottk\OneDrive\GITHUB\calma-esse-heat-stress-internal\Esse\data\processed\2024-04-01_1418_Cozie_main_df.csv


C:\Users\gottk\AppData\Local\Temp\ipykernel_25372\1221405828.py:25: DtypeWarning:

Columns (1,2,3,4,5,6,7,8,9,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,41,42,43,44,48,50,54,55,57,58,60,61,63,64,66,67,69,70,73,75,77,78,80,81,83,84,86,87,89,90,92,93,94,96,97,99,100,102,103,105,106,108,109,111,112,115,117,119,120,122,123,125,126,128,129,131,132,134,135,137,138,139,140,142,143,145,146,147,148,151,152,154,156,159,164,166,167,169,170,172,173,175,176,178,179,181,182,184,185,187,188,190,191,193,194,196,197,199,200,214,215,217,218) have mixed types. Specify dtype option on import or set low_memory=False.

C:\Users\gottk\AppData\Local\Temp\ipykernel_25372\1221405828.py:26: DtypeWarning:

Columns (1,2,3,4,5,6,7,8,9,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,41,42,43,44,48,50,54,55,57,58,60,61,63,64,66,67,69,70,73,75,77,78,80,81,83,84,86,87,89,90,92,93,94,96,97,99,100,102,103,105,106,108,109,111,112,115,117,119,120,

participant_id            timestamp_lambda  ws_longitude  ws_latitude  \
0             esse14  2024-02-21 07:43:42.698727           NaN          NaN   
1             esse14  2024-02-21 07:44:21.821735    103.770868     1.297063   
2             esse14  2024-03-04 07:56:10.041547           NaN          NaN   
3             esse14  2024-02-21 08:20:02.811540           NaN          NaN   
4             esse14  2024-03-04 07:55:21.924528           NaN          NaN   
...              ...                         ...           ...          ...   
27472         esse14  2024-03-27 14:00:53.113560           NaN          NaN   
27473         esse14  2024-03-27 14:00:14.439842    103.771983     1.298510   
27474         esse14  2024-03-27 14:00:59.248009           NaN          NaN   
27475         esse14  2024-03-27 14:00:59.242351           NaN          NaN   
27476         esse14  2024-03-27 14:00:39.034556    103.772030     1.298481   

       ws_survey_count q_general_location_envi    c_difference_time_ws  \
0                  NaN                     NaN                     NaN   
1                  0.0                  Indoor                     NaN   
2                  NaN                     NaN                     NaN   
3                  NaN                     NaN                     NaN   
4                  NaN                     NaN                     NaN   
...                ...                     ...                     ...   
27472              NaN                     NaN                     NaN   
27473            100.0            Semi-Outdoor  0 days 00:22:59.156839   
27474              NaN                     NaN                     NaN   
27475              NaN                     NaN                     NaN   
27476            101.0            Semi-Outdoor  0 days 00:00:24.594714   

       c_distance_ws  c_ws_step_count  c_movespeed  \
0                NaN              NaN          NaN   
1                NaN              NaN          NaN   
2                NaN              NaN          NaN   
3                NaN              NaN          NaN   
4                NaN              NaN          NaN   
...              ...              ...          ...   
27472            NaN              NaN          NaN   
27473            6.0              NaN         0.26   
27474            NaN              NaN          NaN   
27475            NaN              NaN          NaN   
27476            6.0              NaN        14.64   

      flag_q_general_location_envi flag_speed_threshold flag_steps_threshold  \
0                              NaN                  NaN                  NaN   
1                              NaN                  NaN                  NaN   
2                              NaN                  NaN                  NaN   
3                              NaN                  NaN                  NaN   
4                              NaN                  NaN                  NaN   
...                            ...                  ...                  ...   
27472                          NaN                  NaN                  NaN   
27473                          NaN                  NaN            StepCount   
27474                          NaN                  NaN                  NaN   
27475                          NaN                  NaN                  NaN   
27476                          NaN                  NaN            StepCount   

      flag_distance_threshold flag_time_threshold  flag_data_retrieved  \
0                         NaN                 NaN                  NaN   
1                         NaN                 NaN                  NaN   
2                         NaN                 NaN                  NaN   
3                         NaN                 NaN                  NaN   
4                         NaN                 NaN                  NaN   
...                       ...                 ...                  ...   
27472                     NaN           

In [9]:
# <--- Plotly Graphs --->
#Plot geo location of responses
# Create a list to store latitude and longitude data
#add the filter on campus and outdoor and valid
# Assuming you have new_df with columns 'ws_latitude' and 'ws_longitude'

# Assuming you have new_df with columns 'participant_id', 'ws_latitude', and 'ws_longitude'


# Assuming you have new_df with columns 'participant_id', 'ws_latitude', 'ws_longitude', and 'in_study_region'


# Latitude and Longitude of Singapore
singapore_lat = 1.3521
singapore_lon = 103.8198

# Group new_df by participant_id
grouped_df = new_df.groupby('participant_id')

# Create a color scale using a gradient
color_scale = np.linspace(0, 1, len(grouped_df))

# Create a scatter plot
fig = go.Figure()

# Iterate over groups
for idx, (participant_id, group) in enumerate(grouped_df):
    # Determine color based on position in color scale
    color = f'hsl({color_scale[idx] * 360}, 50%, 50%)'
    
    # Check if there are any data points to plot
    if not group.empty:
        hover_text = [
            f"Index: {index + 2}<br>" +
            '<br>'.join(f"{column}: {value}" for column, value in row.items())
            for index, row in group[
                ['flag_q_general_location_envi', 'flag_speed_threshold', 
                'flag_steps_threshold', 'flag_distance_threshold',
                'flag_time_threshold', 'flag_data_retrieved',
                'in_study_region', "timestamp_lambda"]].astype(str).iterrows()
        ]
        fig.add_trace(go.Scattermapbox(
            lat=group['ws_latitude'],
            lon=group['ws_longitude'],
            mode='markers',
            marker=go.scattermapbox.Marker(
                size=9,
                color=color
            ),
            name=participant_id,  # Include participant ID in legend
            hovertext=hover_text,
            hoverinfo='text'
        ))

# Customize layout
fig.update_layout(
    mapbox=dict(
        style="carto-positron",  # Set the style to "carto-positron" for grey
        center=go.layout.mapbox.Center(
            lat=singapore_lat,
            lon=singapore_lon,
        ),
        zoom=10,  # Adjust the zoom level as needed
    ),
    legend=dict(
        title="Participant ID",
    ),
    width=1800,  # Adjust the width of the plot
    height=800,  # Adjust the height of the plot
)

# Show the plot
fig.show()
#To do
#add another graph of average time difference between run points, excuding the time between runs. Group by run, set first index time to nan.
# Get the count of non-null values in each column
# Assuming you have new_df with columns 'participant_id', 'flag_q_general_location_envi', 'flag_speed_threshold', 
# 'flag_steps_threshold', 'flag_distance_threshold', 'flag_time_threshold', 'flag_data_retrieved', 
# and 'in_study_region'

# Group new_df by participant_id
grouped_df = new_df.groupby('participant_id')

# Initialize dictionaries to store counts for each column
column_counts = {col: [] for col in ['flag_q_general_location_envi', 'flag_speed_threshold', 
                                     'flag_steps_threshold', 'flag_distance_threshold',
                                     'flag_time_threshold', 'flag_data_retrieved', 
                                     'in_study_region']}
participants = []

# Iterate over groups and calculate counts for each column
for participant_id, group in grouped_df:
    participants.append(participant_id)
    for col in column_counts.keys():
        column_counts[col].append(group[col].count())

# Create a stacked bar chart
fig = go.Figure()

for col in column_counts.keys():
    fig.add_trace(go.Bar(
        x=participants,
        y=column_counts[col],
        name=col
    ))

# Customize layout
fig.update_layout(
    title="Count of Non-Null Values by Participant",
    xaxis_title="Participant ID",
    yaxis_title="Count",
    barmode='stack'
)

# Show the plot
fig.show()


####################################################
# Filter the DataFrame where 'in_study_region' has a value and 'flag_q_general_location_envi' is empty
filtered_df = new_df[(new_df['in_study_region'].notna()) & (new_df['flag_q_general_location_envi'].isna())]

# Group filtered_df by participant_id
grouped_df = filtered_df.groupby('participant_id')

# Initialize dictionaries to store counts for each column
column_counts = {col: [] for col in [ 'flag_speed_threshold', 'flag_distance_threshold', 'flag_steps_threshold',
                                     'flag_time_threshold', 'flag_data_retrieved']}
participants = []

# Iterate over groups and calculate counts for each column
for participant_id, group in grouped_df:
    participants.append(participant_id)
    for col in column_counts.keys():
        column_counts[col].append(group[col].count())

# Create a stacked bar chart
fig = go.Figure()

for col in column_counts.keys():
    fig.add_trace(go.Bar(
        x=participants,
        y=column_counts[col],
        name=col
    ))

# Customize layout
fig.update_layout(
    title="Count of Non-Null Values by Participant (In Study Region and Empty flag_q_general_location_envi)",
    xaxis_title="Participant ID",
    yaxis_title="Count",
    barmode='stack'
)

# Show the plot
fig.show()
#Bar plot with total responses per day and valid and invalid responses 
    
#One graph 

In [ ]:
# Group filtered_df by participant_id
#filtered_df = new_df[(new_df['in_study_region'].notna()) & (new_df['flag_q_general_location_envi'].isna())]
# Filter new_df to retain 'participant_id' column
filtered_df = new_df[new_df['q_general_location_envi'].notna()]
# Group filtered_df by participant_id
grouped_df = filtered_df.groupby('participant_id')

# Initialize dictionaries to store counts for valid and invalid data
valid_counts = {}
invalid_counts = {}
participants = []

# Iterate over groups and calculate counts for valid and invalid data
for participant_id, group in grouped_df:
    participants.append(participant_id)
    valid_counts[participant_id] = sum(group[[ 'flag_data_retrieved', 'flag_q_general_location_envi', 'flag_time_threshold']].isna().all(axis=1)) #'flag_distance_threshold',
    invalid_counts[participant_id] = len(group) - valid_counts[participant_id]

# Create a stacked bar chart
fig = go.Figure()

fig.add_trace(go.Bar(
    x=participants,
    y=list(valid_counts.values()),
    text=list(valid_counts.values()),  # Text to be displayed on valid data bars
    textposition='outside',  # Automatically position the text
    name="Valid Data",
    marker_color='green'
))

fig.add_trace(go.Bar(
    x=participants,
    y=list(invalid_counts.values()),
    text=list(invalid_counts.values()),  # Text to be displayed on invalid data bars
    textposition='outside',  # Automatically position the text
    name="Invalid Data",
    marker_color='red'
))

# Customize layout
fig.update_layout(
    title="Count of Valid and Invalid Data by Participant (with ws_survey_count)",
    xaxis_title="Participant ID",
    yaxis_title="Count",
    barmode='stack'
)

# Show the plot
fig.show()

In [ ]:
# Convert JSON data to DataFrame


%store -r json_data
print(json_data)

grouped_df = new_df.groupby('participant_id')

nodes = []
links = []

for question_data in json_data['survey']:
    question_id = question_data['question_id']
    question = question_data['question']
    response_options = question_data['response_options']
    
    # Add question as a node
    nodes.append({'label': question_id})
    
    # Add response options as links
    for response_option in response_options:
        response_text = response_option['text']
        next_question_id = response_option['next_question_id']
        
        # Add link
        links.append({
            'source': question_id,
            'target': next_question_id,
            'value': 1  # You can adjust this value based on your requirements
        })

# Create DataFrame for nodes and links
nodes_df = pd.DataFrame(nodes)
links_df = pd.DataFrame(links)

# Create Sankey diagram
fig = go.Figure(data=[go.Sankey(
    node=dict(
        pad=15,
        thickness=20,
        line=dict(color="black", width=0.5),
        label=nodes_df['label'],
    ),
    link=dict(
        source=links_df['source'],
        target=links_df['target'],
        value=links_df['value']
    ))])

fig.update_layout(title_text="Sankey Diagram of Survey Responses")
fig.show()

In [ ]:
# <--- Graph: Timings for when data got recorded --->
#Define a list of parameters to check
lst_columns_data = ['ws_heart_rate', 'ts_heart_rate']
lst_columns = ['timestamp_lambda'] + lst_columns_data
# Create the new DataFrame by selecting the specified columns
df_recorded_data = participant_data_local['esse07'][lst_columns]

df_recorded_data['Flag'] = 'NaN'  # Initialize flag column with default value '2'

for column_header in lst_columns_data:  # Iterating over column headers in lst_columns_data
    df_recorded_data.loc[~df_recorded_data[column_header].isna(), 'Flag'] = '1'  # Set flag to '1' where non-NaN values exist

# Then, we select those columns from df_recorded_data and convert them to numeric
columns_to_convert = lst_columns_data + ['Flag']
df_recorded_data[columns_to_convert] = df_recorded_data[columns_to_convert].apply(pd.to_numeric, errors='coerce')

# Convert timestamp_lambda to datetime format
df_recorded_data['timestamp_lambda'] = pd.to_datetime(df_recorded_data['timestamp_lambda'])

# Extract the date and hour from timestamp_lambda
df_recorded_data['date'] = df_recorded_data['timestamp_lambda'].dt.date
df_recorded_data['hour'] = df_recorded_data['timestamp_lambda'].dt.hour

# Convert 'date' column to datetime objects
df_recorded_data['date'] = pd.to_datetime(df_recorded_data['date'])

df_recorded_data_group = df_recorded_data[['date', 'Flag']].groupby('date').sum()
display(df_recorded_data_group)
# Define the date range
start_date = '2024-01-15'
end_date = '2024-02-10'

# Convert start_date and end_date to datetime objects
start_date = pd.to_datetime(start_date)
end_date = pd.to_datetime(end_date)

# Filter df_recorded_data to include only dates within the specified range
df_filtered = df_recorded_data[(df_recorded_data['date'] >= start_date) & (df_recorded_data['date'] <= end_date)]

# Create a boxplot for each day
plt.figure(figsize=(15, 8))
sns.boxplot(x='date', y='hour', data=df_filtered, showfliers=False)  # Set showfliers=False to exclude outliers
sns.stripplot(x='date', y='hour', data=df_filtered, jitter=0.1, color='black', alpha=0.5, size=3)  # Set jitter=0.1 for slight horizontal displacement
plt.title('Timings for when data got recorded')
plt.xlabel('Date')
plt.ylabel('Hour of the day')
plt.xticks(rotation=90, ha='center')  # Rotate x labels for better readability
plt.tight_layout()
plt.show()


In [ ]:
#TODO Diagrams
#Time when data is retreived, when participants wear the watches, when do they do surveys?

#display(participant_data_local['esse00']['timestamp_lambda'])
#time_columns = [col for col in participant_data_local['esse00'].columns if 'time' in col]
#pprint(time_columns)
#need dataframe taht shows the date DDMMYY - rounded and than just the time in HH:MM - another column with data to color in ?

column_lst_items = ['timestamp', 'ws_survey_count']
#Add another list that defines if it should sum or count? Useful?

#-----------------------------------------------------------------------------------
# Assuming df contains your DataFrame
df = participant_data_local['esse00'][['timestamp_lambda', 'ws_heart_rate', 'ts_heart_rate']]

# Combine heart rate columns
df['combined_heart_rate'] = df['ws_heart_rate'].fillna(df['ts_heart_rate'])
df = df['combined_heart_rate'].dropna()

# Merge with timestamp data
df = pd.merge(df, participant_data_local['esse00']['timestamp_lambda'], left_index=True, right_index=True, how='inner')
display(df)
# Convert timestamp to datetime
df['timestamp_lambda'] = pd.to_datetime(df['timestamp_lambda'])

# Extract date in DDMMYY format
df['Date_DDMMYY'] = df['timestamp_lambda'].dt.strftime('%d%m%y')

# Extract time in HHMM format
df['Time_HHMM'] = df['timestamp_lambda'].dt.strftime('%H%M')

# Convert 'Date_DDMMYY' to datetime
df['Date_DDMMYY'] = pd.to_datetime(df['Date_DDMMYY'], format='%d%m%y')

# Convert 'Time_HHMM' to datetime
#df['Time_HHMM'] = pd.to_datetime(df['Time_HHMM'], format='%H%M')

